In [1]:
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
import nltk
from nltk import word_tokenize
from sklearn import model_selection
from sklearn.feature_extraction.text import TfidfVectorizer

from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.naive_bayes import GaussianNB, MultinomialNB
from sklearn.metrics import accuracy_score, hamming_loss, classification_report

from skmultilearn.adapt import MLkNN

In [2]:
data = pd.read_csv('csv/train_01.csv')

In [3]:
data.head()

id                                       comment_text  toxic  \
0  0000997932d777bf  explan edit made username hardcore metallica f...      0   
1  000103f0d9cfb60f  d'aww! match background colour i'm seemingly s...      0   
2  000113f07ec002fd  hey man, i'm really tri edit war guy constantl...      0   
3  0001b41b1c6bb37e  " can't make real suggest improv wonder sectio...      0   
4  0001d958c54c6e35         you, sir, hero chance rememb page that on?      0   

   severe_toxic  obscene  threat  insult  identity_hate  
0             0        0       0       0              0  
1             0        0       0       0              0  
2             0        0       0       0              0  
3             0        0       0       0              0  
4             0        0       0       0              0

In [4]:
data[data.isnull().any(axis=1)]
# ovo su komentari koji su bili prazni

id comment_text  toxic  severe_toxic  obscene  threat  \
228     0091798f05a311af          NaN      0             0        0       0   
329     00d300b2a1d61c1c          NaN      0             0        0       0   
3699    09e4ea8663421151          NaN      0             0        0       0   
3990    0aa6f3529219b37e          NaN      0             0        0       0   
4482    0bed2196c873636d          NaN      0             0        0       0   
...                  ...          ...    ...           ...      ...     ...   
153616  9fe2529bbf1aa64a          NaN      0             0        0       0   
154268  ab68b24628bbe30e          NaN      0             0        0       0   
156776  d3741a61f9c91ac0          NaN      0             0        0       0   
158092  e8a55975186094fe          NaN      0             0        0       0   
159315  fbf8672ea3b4ddf7          NaN      1             0        0       0   

        insult  identity_hate  
228          0              0  
329          0              0  
3699         0              0  
3990         0              0  
4482         0              0  
...        ...            ...  
153616       0              0  
154268       0              0  
156776       0              0  
158092       0              0  
159315       0              0  

[118 rows x 8 columns]

In [5]:
data = data.dropna(how='any',axis=0) 

In [6]:
data['comment_text'].isnull().any()

False

In [7]:
data_text = data['comment_text'].values.astype('U')
X = data.drop(labels=['id'], axis=1)
y = data.drop(labels = ['id', 'comment_text'], axis=1)

In [8]:
X_train, X_test, y_train, y_test = model_selection.train_test_split(X, y, test_size = 0.33, random_state=42)

### Feature Engineering

https://www.youtube.com/watch?v=YyOuDi-zSiI

https://medium.com/technovators/machine-learning-based-multi-label-text-classification-9a0e17f88bb4

In [9]:
vectorizer = TfidfVectorizer(strip_accents='unicode', tokenizer=word_tokenize, analyzer='word', ngram_range=(1,3), norm='l2', max_features = 10000)

In [10]:
X_train_vec = vectorizer.fit_transform(X_train['comment_text'])

In [11]:
X_test_vec = vectorizer.transform(X_test['comment_text'])

In [12]:
features = vectorizer.get_feature_names()
features

['!',
 '! !',
 '! ! !',
 "! ! '",
 "! ! ''",
 "! ! 'fuck",
 '! ! )',
 '! ! ``',
 '! ! access',
 '! ! fuck',
 '! ! hi',
 '! ! i',
 '! ! jim',
 '! ! person',
 '! ! please',
 '! ! u',
 "! '",
 "! ' u",
 "! ''",
 "! '' ''",
 "! 'fuck",
 "! 'fuck you",
 '! (',
 '! ( talk',
 '! )',
 '! ) ,',
 '! ) ``',
 '! ,',
 '! ?',
 '! ? !',
 '! ``',
 '! `` ``',
 '! access',
 '! access deneid',
 '! also',
 '! block',
 '! block you',
 '! bunksteve',
 '! bunksteve gay',
 '! eat',
 '! eat cock',
 '! f',
 '! f uu',
 '! fuck',
 '! fuck all',
 '! fuck bitch',
 '! fuck cocksuck',
 '! fuck fired',
 '! fuck you',
 '! get',
 '! go',
 '! go fuck',
 '! good',
 '! haahhahahah',
 '! haahhahahah yaaa',
 '! heil',
 '! heil hitler',
 '! hello',
 '! hello ,',
 '! hi',
 '! hi wikipedia',
 '! hope',
 '! i',
 "! i 'm",
 "! i 've",
 '! in',
 '! in name',
 '! jim',
 '! jim wale',
 '! know',
 '! know you',
 '! lol',
 '! look',
 '! mangina',
 '! mangina !',
 '! mothjer',
 '! mothjer fucker',
 '! oh',
 '! oh bob',
 '! old',
 '! ol

In [13]:
vectorizer.vocabulary_

{'``': 1401,
 'image': 5076,
 'copyright': 3142,
 'problem': 7238,
 'gif': 4559,
 'thank': 8807,
 'upload': 9227,
 'identifi': 5052,
 'specifi': 8327,
 'status': 8413,
 ',': 587,
 'requir': 7664,
 'wikipedia': 9657,
 'policy': 7102,
 'indicate': 5191,
 'imag': 5073,
 'descript': 3504,
 'page': 6694,
 'use': 9249,
 'appropriate': 1945,
 'tag': 8643,
 'may': 5958,
 'delet': 3415,
 'time': 8956,
 'next': 6338,
 'seven': 8042,
 'day': 3342,
 'images': 5102,
 'please': 7007,
 'verify': 9396,
 'provid': 7308,
 'inform': 5205,
 'well': 9580,
 'see': 7947,
 'follow': 4311,
 'autom': 2203,
 'notice': 6452,
 'assistance': 2149,
 'media': 6013,
 'question': 7365,
 'hi': 4853,
 'ad': 1624,
 'fair': 4126,
 'seem': 7981,
 'subject': 8496,
 'howev': 4959,
 'need': 6278,
 'state': 8399,
 'source': 8274,
 'own': 6675,
 'cool': 3132,
 'way': 9523,
 'thanks': 8838,
 '!': 0,
 'sockpuppet': 8215,
 'think': 8889,
 'move': 6178,
 'talk': 8691,
 'one': 6568,
 'longer': 5782,
 '(': 405,
 'the': 8850,
 'main': 

In [14]:
#from yellowbrick.text import FreqDistVisualizer
#visualizer = FreqDistVisualizer(features=features, orient='v')
#visualizer.fit(X_train_vec)
#visualizer.show()

In [15]:
import pickle

pickle.dump(vectorizer, open("vectorizer_01.pickle", "wb"))

In [42]:
from sklearn.multiclass import OneVsRestClassifier
from sklearn.svm import LinearSVC

clf = OneVsRestClassifier(LinearSVC(), n_jobs=1)

In [43]:
clf.fit(X_train_vec, y_train)

OneVsRestClassifier(estimator=LinearSVC(), n_jobs=1)

In [44]:
score = clf.score(X_train_vec, y_train)

In [45]:
pred = clf.predict(X_test_vec)

In [47]:
score

0.9502588151601097

In [49]:
clf.score(X_test_vec,y_test)

0.9152223489167617

In [50]:
k = 0
for p in pred:
    if p[0] ==1 or p[1] == 1 or p[2]==1 or  p[3]==1:
        print(p)
        print(X_test.iloc[k])
    k= k+1    


[1 0 1 0 1 0]
id                                                c4a84ed9045b8b28
comment_text     harrasing?who personally attacking?i said dumb...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          1
threat                                                           0
insult                                                           0
identity_hate                                                    0
Name: 132438, dtype: object
[1 0 0 0 0 0]
id                                                2a3a71b81375a308
comment_text     " ""vandalism"" queer page honest think contri...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          0
threat                                                           0
insult

Name: 133350, dtype: object
[1 0 1 0 1 0]
id               1d120020d3098a7c
comment_text           life bitch
toxic                           1
severe_toxic                    0
obscene                         1
threat                          0
insult                          0
identity_hate                   0
Name: 10997, dtype: object
[1 0 1 0 1 0]
id               65aa83b7f2e856c0
comment_text      fuck mess total
toxic                           1
severe_toxic                    0
obscene                         1
threat                          0
insult                          0
identity_hate                   0
Name: 114749, dtype: object
[1 0 0 0 0 0]
id                                                3e010c1c093f925a
comment_text     " right, fine even start discuss join every ti...
toxic                                                            1
severe_toxic                                                     0
obscene                                                        

Name: 144954, dtype: object
[1 0 1 0 1 0]
id                                                f0d45f5597066a49
comment_text     hey dumb bitch cant spell saturn girl well lin...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          1
threat                                                           0
insult                                                           1
identity_hate                                                    0
Name: 90021, dtype: object
[1 0 1 0 1 0]
id                                                e75b03c51805e23d
comment_text     fuck meno! retard twat, virgin every cool thin...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          1
threat                                        

Name: 32101, dtype: object
[1 0 0 0 0 0]
id                                                96b2c8013ef97dac
comment_text     let tell little man, person attack find beat h...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          0
threat                                                           1
insult                                                           0
identity_hate                                                    0
Name: 153053, dtype: object
[1 0 0 0 0 0]
id                                       11cc215d1ac61b7f
comment_text     nick movie suck busi go find someth else
toxic                                                   1
severe_toxic                                            0
obscene                                                 1
threat                                                  0
insult                           

[1 0 0 1 1 0]
id                                                02c2f3e834144014
comment_text     i'm go kill i'm serious retard loser deserve d...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          0
threat                                                           1
insult                                                           0
identity_hate                                                    0
Name: 96240, dtype: object
[1 0 1 0 0 0]
id                                                672b9bf5fe6ed7f4
comment_text     i'll happily dance wikipedia grave shutdown ha...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          0
threat                                                           0
insult 

...

Name: 112483, dtype: object
[1 0 0 0 0 1]
id                 71c6a5551bc1b17e
comment_text     think gay well he?
toxic                             1
severe_toxic                      0
obscene                           0
threat                            0
insult                            0
identity_hate                     0
Name: 42632, dtype: object
[1 0 1 0 0 1]
id                                                c457f6f7ed8227cb
comment_text     pick palestinian baby homosexu countrymen, wor...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          1
threat                                                           0
insult                                                           1
identity_hate                                                    1
Name: 73390, dtype: object
[1 0 0 0 0 0]
id                                                8f

[1 0 1 0 1 0]
id                                944a4e8698b829ae
comment_text     hello dick wikipedia fuckwhit ban
toxic                                            1
severe_toxic                                     0
obscene                                          1
threat                                           0
insult                                           1
identity_hate                                    0
Name: 123440, dtype: object
[1 0 0 0 0 0]
id                                                0a49087b1e1f3c78
comment_text     anonym lady, hound block dick gave fact though...
toxic                                                            0
severe_toxic                                                     0
obscene                                                          1
threat                                                           0
insult                                                           0
identity_hate                                                    0


Name: 123697, dtype: object
[1 0 0 0 0 0]
id                                                f3e9e82375d0be95
comment_text     " welcome reality check protect page moron com...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          0
threat                                                           0
insult                                                           0
identity_hate                                                    0
Name: 141289, dtype: object
[1 1 1 0 1 0]
id               b67b41e7d8acc29f
comment_text          bitch cunt!
toxic                           1
severe_toxic                    1
obscene                         1
threat                          0
insult                          1
identity_hate                   1
Name: 129827, dtype: object
[1 0 0 0 0 1]
id                  2f3cb8e059f6205b
comment_text     really gay l

Name: 134599, dtype: object
[1 0 1 0 1 0]
id                              0c02c16bee1c70e2
comment_text     asshole yep suck jesus suberbia
toxic                                          1
severe_toxic                                   0
obscene                                        1
threat                                         0
insult                                         1
identity_hate                                  0
Name: 4513, dtype: object
[1 0 1 0 1 0]
id               302ba7d0c8e2e210
comment_text         itnc go fuck
toxic                           1
severe_toxic                    1
obscene                         1
threat                          0
insult                          1
identity_hate                   0
Name: 18246, dtype: object
[1 0 0 0 0 0]
id                                                6ef22c0a8863b6c0
comment_text     " (utc) wrong, banana use use ripe one find so...
toxic                                                            1
severe_toxic

Name: 152601, dtype: object
[1 1 1 0 1 0]
id                                                fc7b5a2e7deaf321
comment_text     get fuck maggot dog fuck shit website fuck noo...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          1
threat                                                           0
insult                                                           1
identity_hate                                                    0
Name: 94413, dtype: object
[1 0 1 0 1 0]
id                                a3d59280a1685a04
comment_text     asshole, bring everyth tell me!!!
toxic                                            1
severe_toxic                                     0
obscene                                          1
threat                                           0
insult                                           1
identity_hate           

In [60]:
test_unseen = pd.read_csv('csv/test_01.csv')
test_labels = pd.read_csv('csv/test_labels.csv')

test_text = test_unseen['comment_text'].values.astype('U')

unseen_data = pd.merge(test_unseen,test_labels,on="id")
unseen_data = unseen_data.dropna(how='any',axis=0)
unseen_data = unseen_data[unseen_data["toxic"] != -1]
unseen_data

id                                       comment_text  \
5       0001ea8717f6de06  thank understand think highly would revert wit...   
7       000247e83dcc1211                             dear god site horrible   
11      0002f87b16116a7f  " somebody invariably try add religion? really...   
13      0003e1cccfd5a40a  " say right type ""type"" institut need case t...   
14      00059ace3e3e9a53  " ad new product list, make sure relev ad new ...   
...                  ...                                                ...   
153150  fff8f64043129fa2  jerome, see never got around ! surpris look ex...   
153151  fff9d70fe0722906         lucky bastard heh famous kida envy congrat   
153154  fffa8a11c4378854               shame all!!! want speak gay romanian   
153155  fffac2a094c8e0e2  mel gibson nazi bitch make shitty movie much b...   
153156  fffb5451268fb5ba  " unicorn lair discovery supposedly, unicorn l...   

        toxic  severe_toxic  obscene  threat  insult  identity_hate  
5           0             0        0       0       0              0  
7           0             0        0       0       0              0  
11          0             0        0       0       0              0  
13          0             0        0       0       0              0  
14          0             0        0       0       0              0  
...       ...           ...      ...     ...     ...            ...  
153150      0             0        0       0       0              0  
153151      0             0        0       0       0              0  
153154      0             0        0       0       0              0  
153155      1             0        1       0       1              0  
153156      0             0        0       0       0              0  

[63711 rows x 8 columns]

In [54]:
y_unseen = unseen_data.drop(labels = ['id', 'comment_text'], axis=1)
X_test_unseen = vectorizer.transform(unseen_data['comment_text'])

In [55]:
pred_unseen =  clf.predict(X_test_unseen)

In [56]:
clf.score(X_test_unseen,y_unseen)

0.8827204093484642

In [57]:
k = 0
for p in pred_unseen:
    if p[0] ==1 or p[1] == 1 or p[2]==1 or  p[3]==1:
        print(p)
        print(unseen_data.iloc[k])
    k= k+1    

[1 0 1 0 1 0]
id                                                001068b809feee6b
comment_text     " balance page one sentence basic definit word...
toxic                                                            0
severe_toxic                                                     0
obscene                                                          0
threat                                                           0
insult                                                           0
identity_hate                                                    0
Name: 38, dtype: object
[1 0 1 0 1 0]
id                                        0013fed3aeae76b7
comment_text     dj robinson gay hell! suck dick much!!!!!
toxic                                                    1
severe_toxic                                             0
obscene                                                  1
threat                                                   0
insult                                                   1

id                                 0ac645ec072a2b85
comment_text     murder micheal shag kill buttercup
toxic                                             0
severe_toxic                                      0
obscene                                           0
threat                                            0
insult                                            0
identity_hate                                     0
Name: 6424, dtype: object
[1 0 1 0 1 0]
id                                               0ac92b4a72248de1
comment_text     fine fuck it! i'm sick cyberbulli look like shit
toxic                                                           1
severe_toxic                                                    0
obscene                                                         1
threat                                                          0
insult                                                          1
identity_hate                                                   0
Name: 6431, dtyp

Name: 11402, dtype: object
[1 0 1 0 0 0]
id                                                133b1b62dcd453db
comment_text     " would told ""shut fuck whine twat""? probabl...
toxic                                                            0
severe_toxic                                                     0
obscene                                                          0
threat                                                           0
insult                                                           0
identity_hate                                                    0
Name: 11469, dtype: object
[1 0 1 0 0 0]
id                  133e6a2ec1b42af1
comment_text     hello dude dick fix
toxic                              1
severe_toxic                       0
obscene                            1
threat                             0
insult                             1
identity_hate                      0
Name: 11482, dtype: object
[1 0 1 0 1 0]
id               13429fcdb2b1697f
comment_tex

id                1af9b701b468a7f8
comment_text     maybe get life!!!
toxic                            0
severe_toxic                     0
obscene                          0
threat                           0
insult                           0
identity_hate                    0
Name: 16075, dtype: object
[1 0 1 0 0 0]
id                                                1b04bafe1737c034
comment_text     second apologise language here, i'm absolutely...
toxic                                                            0
severe_toxic                                                     0
obscene                                                          0
threat                                                           0
insult                                                           0
identity_hate                                                    0
Name: 16099, dtype: object
[1 0 1 0 1 0]
id                                                1b05b55f481f4aca
comment_text     stop undo edit dum

[1 0 0 0 1 0]
id               24b090b3de391ff8
comment_text          hola ur fat
toxic                           1
severe_toxic                    0
obscene                         0
threat                          0
insult                          0
identity_hate                   0
Name: 21980, dtype: object
[1 1 1 0 1 0]
id                     24b3fb89f4dc0003
comment_text     fuck jewish piece shit
toxic                                 1
severe_toxic                          0
obscene                               1
threat                                0
insult                                1
identity_hate                         1
Name: 21983, dtype: object
[1 0 0 0 1 0]
id                                                24b500cc97847b31
comment_text     whay hell write what grandfath name talkpage (...
toxic                                                            1
severe_toxic                                                     0
obscene                                     

...

[1 0 0 0 0 0]
id                                                e18b3069ca243d6f
comment_text     disappointing, he rex answer is, that stupid c...
toxic                                                            0
severe_toxic                                                     0
obscene                                                          0
threat                                                           0
insult                                                           0
identity_hate                                                    0
Name: 134922, dtype: object
[1 0 1 0 0 0]
id                    e193361017701a92
comment_text     article like bullshit
toxic                                1
severe_toxic                         0
obscene                              1
threat                               0
insult                               0
identity_hate                        0
Name: 134949, dtype: object
[1 0 1 0 1 0]
id                            e19d3a2ad6ce9089
comment

id                                                e9f19840b558a26a
comment_text     " anoth remind matter want twist logic, main i...
toxic                                                            0
severe_toxic                                                     0
obscene                                                          0
threat                                                           0
insult                                                           0
identity_hate                                                    0
Name: 139936, dtype: object
[1 0 0 0 0 0]
id                            e9f2c9c8f60f10a1
comment_text     hej fmid ng b g f ngf hmh jul
toxic                                        0
severe_toxic                                 0
obscene                                      0
threat                                       0
insult                                       0
identity_hate                                0
Name: 139941, dtype: object
[1 0 1 0 1 0]
id  

Name: 143880, dtype: object
[1 0 0 0 0 0]
id                                                f074bc5d09c523e2
comment_text     see profile, jschnur (if real name) profoundly...
toxic                                                            0
severe_toxic                                                     0
obscene                                                          0
threat                                                           0
insult                                                           0
identity_hate                                                    0
Name: 143882, dtype: object
[1 0 0 0 0 0]
id                                                f07e18fcc27a557d
comment_text     hell confirm sabu go world heavey weight title...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          1
threat                                       

Name: 148052, dtype: object
[1 0 0 0 0 0]
id                                                f777afae2dc5b633
comment_text     " see wp notcensor wikipedia written children ...
toxic                                                            0
severe_toxic                                                     0
obscene                                                          0
threat                                                           0
insult                                                           0
identity_hate                                                    0
Name: 148060, dtype: object
[1 0 1 0 1 0]
id                                                f77b3160efb88139
comment_text     useless cunt send anymore message i'll brick c...
toxic                                                            1
severe_toxic                                                     1
obscene                                                          1
threat                                       

Name: 152074, dtype: object
[1 0 1 0 0 0]
id                                                fe1f6e31f5cb2bc5
comment_text     bristol parkway railway station never fuck agr...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          1
threat                                                           0
insult                                                           1
identity_hate                                                    0
Name: 152075, dtype: object
[1 0 1 0 0 0]
id                                                fe298049d313fabe
comment_text     open shut case bathroom knox walk fuck excuse?...
toxic                                                            0
severe_toxic                                                     0
obscene                                                          0
threat                                       